In [3]:
from transformers import pipeline
classifier = pipeline("text-classification",model='bhadresh-savani/distilbert-base-uncased-emotion', return_all_scores=True)
prediction = classifier("I love using transformers. The best part is wide range of support and its easy to use", )
print(prediction)

/Users/meenakshigopalakrishnan/anaconda3/envs/characterPlaylistGenerator/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/Users/meenakshigopalakrishnan/anaconda3/envs/characterPlaylistGenerator/lib/python3.12/site-packages/transformers/pipelines/text_classification.py:104: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(


[[{'label': 'sadness', 'score': 0.00067926972405985}, {'label': 'joy', 'score': 0.9959298968315125}, {'label': 'love', 'score': 0.0009452439262531698}, {'label': 'anger', 'score': 0.0018055178225040436}, {'label': 'fear', 'score': 0.000411103421356529}, {'label': 'surprise', 'score': 0.00022885671933181584}]]


In [4]:
from tqdm import tqdm
tqdm.pandas()

In [5]:
import pandas as pd

In [29]:
song_df = pd.read_csv('spotify_millsongdata.csv')
movie_df = pd.read_csv('wiki_movie_plots_deduped.csv')

In [6]:
import csv

def fix_csv(csv_file, output_file):
    with open(csv_file, 'r', newline='', encoding='utf-8') as infile:
        reader = csv.reader(infile)
        with open(output_file, 'w', newline='', encoding='utf-8') as outfile:
            writer = csv.writer(outfile)
            for row in reader:
                fixed_row = fix_row(row)
                writer.writerow(fixed_row)

def fix_row(row):
    fixed_row = []
    in_quotes = False
    for field in row:
        if in_quotes:
            if field.endswith('"'):
                # Closing quotation mark found
                fixed_row[-1] += field
                in_quotes = False
            else:
                # Inside a quoted string, append as is
                fixed_row[-1] += field + ','
        else:
            if field.startswith('"') and not field.endswith('"'):
                # Opening quotation mark found
                fixed_row.append(field)
                in_quotes = True
            else:
                fixed_row.append(field)
    return fixed_row

fix_csv('finalGeniusLyrica.csv', 'fixed_finalGeniusLyrica.csv')


In [7]:
lyrics_df = pd.read_csv('fixed_finalGeniusLyrica.csv')

In [9]:
def generate_emotion_metrics(text):
    # Define the maximum sequence length
    max_seq_length = 512
    
    # Split the text into chunks
    chunks = [text[i:i+max_seq_length] for i in range(0, len(text), max_seq_length)]
    
    # Initialize dictionaries to store emotion scores
    emotion_scores_combined = {'joy': 0, 'anger': 0, 'love': 0, 'sadness': 0, 'fear': 0, 'surprise': 0}
    
    # Iterate over the chunks and generate emotion scores
    for chunk in chunks:
        classifier = pipeline("text-classification", model='bhadresh-savani/distilbert-base-uncased-emotion', return_all_scores=True)
        emotion_scores = classifier(chunk)
        
        # Aggregate emotion scores from each chunk
        for emotion_score_dict in emotion_scores[0]:
            emotion = emotion_score_dict['label']
            score = emotion_score_dict['score']
            emotion_scores_combined[emotion] += score
    
    # Normalize the aggregated emotion scores
    total_score = sum(emotion_scores_combined.values())
    emotion_metrics = {emotion: score /  total_score for emotion, score in emotion_scores_combined.items()}
    
    return emotion_metrics


In [45]:
import pandas as pd

In [37]:
geniusEmotion = pd.read_csv('geniusEmotion.csv')

In [40]:
geniusEdited = geniusEmotion.drop(columns=["lyrics", "track_id", "artist_id"])

In [41]:
print(geniusEdited)

                                              track_name   artist_name  \
0      All Too Well (10 Minute Version) (Taylor’s Ver...  Taylor Swift   
1      All Too Well (10 Minute Version) (Taylor’s Ver...  Taylor Swift   
2                                               cardigan  Taylor Swift   
3                                                  exile  Taylor Swift   
4                                                  Lover  Taylor Swift   
...                                                  ...           ...   
13239                                             Shmunk          Yeat   
13240                                               ILUV          Yeat   
13241                                            Outsidë          Yeat   
13242                                        Timë Passed          Yeat   
13243                                         Rav3 p4rty          Yeat   

                                         emotion_metrics  
0      {'joy': 0.4940321167029251, 'anger': 0.121765

In [42]:
geniusEdited.columns = ['artist', 'song', 'emotion_metrics']


In [43]:
print(geniusEdited)

                                                  artist          song  \
0      All Too Well (10 Minute Version) (Taylor’s Ver...  Taylor Swift   
1      All Too Well (10 Minute Version) (Taylor’s Ver...  Taylor Swift   
2                                               cardigan  Taylor Swift   
3                                                  exile  Taylor Swift   
4                                                  Lover  Taylor Swift   
...                                                  ...           ...   
13239                                             Shmunk          Yeat   
13240                                               ILUV          Yeat   
13241                                            Outsidë          Yeat   
13242                                        Timë Passed          Yeat   
13243                                         Rav3 p4rty          Yeat   

                                         emotion_metrics  
0      {'joy': 0.4940321167029251, 'anger': 0.121765

In [46]:
df = pd.read_csv("newSongEdited.csv")
final4real = pd.concat([df, geniusEdited], ignore_index=True)
print(final4real)

            artist                   song  \
0             ABBA  Ahe's My Kind Of Girl   
1             ABBA       Andante, Andante   
2             ABBA         As Good As New   
3             ABBA                   Bang   
4             ABBA       Bang-A-Boomerang   
...            ...                    ...   
65991       Shmunk                   Yeat   
65992         ILUV                   Yeat   
65993      Outsidë                   Yeat   
65994  Timë Passed                   Yeat   
65995   Rav3 p4rty                   Yeat   

                                         emotion_metrics  \
0      {'joy': 0.9988289208827446, 'anger': 0.0001545...   
1      {'joy': 0.6534017489030036, 'anger': 0.0038670...   
2      {'joy': 0.6008874079069335, 'anger': 0.0056411...   
3      {'joy': 0.008357059498882647, 'anger': 0.33226...   
4      {'joy': 0.01621546563623756, 'anger': 0.331428...   
...                                                  ...   
65991  {'joy': 0.41044561178565114, 'an

In [47]:
final4real.to_csv("final4real.csv", index=False)

In [16]:
def process_chunk(chunk):
    chunk['emotion_metrics'] = chunk['lyrics'].apply(generate_emotion_metrics)
    return chunk

In [17]:
nan_rows = lyrics_df[lyrics_df['lyrics'].isna()]
print(nan_rows)

                               track_name  track_id           artist_name  \
193                     Like Toy Soldiers       735                Eminem   
1119              Norman fucking Rockwell   3965734          Lana Del Rey   
1994                       Drew Barrymore   2411721                   SZA   
3267                          SUICIDEBOYZ   9739896            Hon Akkori   
3268                   Put Me On... (Rap)   2385311          Genius Users   
3280                            Bez Surce   3334123                Sainty   
3283                        SUICIDEBOMBER   7408967            KILLRIDDLE   
3302                                Rusty    133413    Tyler, The Creator   
3485                      Watching Movies    150336            Mac Miller   
3705                              Flexin’   4966719             Pop Smoke   
4177     See You Again (Original Version)   1788985          Charlie Puth   
4306          Rodeo (Travis Scott Remix)*   4648178             Lil Nas X   

In [18]:
lyrics_df = lyrics_df.dropna(subset=['lyrics'])


In [19]:
print(lyrics_df)

                                              track_name  track_id  \
0      All Too Well (10 Minute Version) (Taylor’s Ver...   7076626   
1      All Too Well (10 Minute Version) (Taylor’s Ver...   7394358   
2                                               cardigan   5793984   
3                                                  exile   5793983   
4                                                  Lover   4508914   
...                                                  ...       ...   
13276                                             Shmunk   8436680   
13277                                               ILUV  10060352   
13278                                            Outsidë   7419506   
13279                                        Timë Passed   9090448   
13280                                         Rav3 p4rty   8657697   

        artist_name  artist_id  \
0      Taylor Swift       1177   
1      Taylor Swift       1177   
2      Taylor Swift       1177   
3      Taylor Swift    

In [10]:
print(lyrics_df)

                                              track_name  track_id  \
0      All Too Well (10 Minute Version) (Taylor’s Ver...   7076626   
1      All Too Well (10 Minute Version) (Taylor’s Ver...   7394358   
2                                               cardigan   5793984   
3                                                  exile   5793983   
4                                                  Lover   4508914   
...                                                  ...       ...   
13276                                             Shmunk   8436680   
13277                                               ILUV  10060352   
13278                                            Outsidë   7419506   
13279                                        Timë Passed   9090448   
13280                                         Rav3 p4rty   8657697   

        artist_name  artist_id  \
0      Taylor Swift       1177   
1      Taylor Swift       1177   
2      Taylor Swift       1177   
3      Taylor Swift    

In [22]:
import math
import tqdm 
chunk_size = 1000

# Calculate the number of chunks
num_chunks = math.ceil(len(lyrics_df) / chunk_size)

# Process the DataFrame in chunks
result_chunks = []
for chunk_idx in tqdm.tqdm(range(int(num_chunks))):
    start_idx = chunk_idx * chunk_size
    end_idx = min((chunk_idx + 1) * chunk_size, len(lyrics_df))
    chunk = lyrics_df.iloc[start_idx:end_idx].copy()
    result_chunks.append(process_chunk(chunk))

# Concatenate the result chunks into the final DataFrame
result_df = pd.concat(result_chunks)

  0%|          | 0/14 [00:00<?, ?it/s]/Users/meenakshigopalakrishnan/anaconda3/envs/characterPlaylistGenerator/lib/python3.12/site-packages/transformers/pipelines/text_classification.py:104: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(
  7%|▋         | 1/14 [1:01:47<13:23:10, 3707.00s/it]/Users/meenakshigopalakrishnan/anaconda3/envs/characterPlaylistGenerator/lib/python3.12/site-packages/transformers/pipelines/text_classification.py:104: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(
 14%|█▍        | 2/14 [1:45:11<10:11:43, 3058.62s/it]/Users/meenakshigopalakrishnan/anaconda3/envs/characterPlaylistGenerator/lib/python3.12/site-packages/transformers/pipelines/text_classifi

In [23]:
print(result_df)

                                              track_name  track_id  \
0      All Too Well (10 Minute Version) (Taylor’s Ver...   7076626   
1      All Too Well (10 Minute Version) (Taylor’s Ver...   7394358   
2                                               cardigan   5793984   
3                                                  exile   5793983   
4                                                  Lover   4508914   
...                                                  ...       ...   
13276                                             Shmunk   8436680   
13277                                               ILUV  10060352   
13278                                            Outsidë   7419506   
13279                                        Timë Passed   9090448   
13280                                         Rav3 p4rty   8657697   

        artist_name  artist_id  \
0      Taylor Swift       1177   
1      Taylor Swift       1177   
2      Taylor Swift       1177   
3      Taylor Swift    

In [24]:
result_df.to_csv('geniusEmotion.csv', index=False)

In [31]:
movie_df = movie_df.drop_duplicates(subset=['Title', 'Plot'])
movie_df = movie_df.drop(['Origin/Ethnicity', 'Wiki Page'], axis=1)
movie_df = movie_df.dropna(subset=['Title', 'Plot'])
movie_df = movie_df[movie_df['Release Year'] > 1950]

In [32]:
print(movie_df)

       Release Year                                       Title  \
5285           1951                             The 13th Letter   
5286           1951  Abbott and Costello Meet the Invisible Man   
5287           1951                             Ace in the Hole   
5288           1951                    Across the Wide Missouri   
5289           1951                Adventures of Captain Fabian   
...             ...                                         ...   
34881          2014                           The Water Diviner   
34882          2017                          Çalgı Çengi İkimiz   
34883          2017                                Olanlar Oldu   
34884          2017                            Non-Transferable   
34885          2017                          İstanbul Kırmızısı   

                      Director  \
5285            Otto Preminger   
5286            Charles Lamont   
5287              Billy Wilder   
5288        William A. Wellman   
5289          William Mar

In [38]:
def mov_process_chunk(chunk):
    chunk['emotion_metrics'] = chunk['Plot'].apply(generate_emotion_metrics)
    return chunk

In [39]:
mov_chunk_size = 1000

# Calculate the number of chunks
mov_num_chunks = len(movie_df) , / mov_chunk_size + 1

# Process the DataFrame in chunks
mov_result_chunks = []
for mov_chunk_idx in tqdm(range(mov_num_chunks)):
    mov_start_idx = mov_chunk_idx * mov_chunk_size
    mov_end_idx = min((mov_chunk_idx + 1) * mov_chunk_size, len(movie_df))
    mov_chunk = movie_df.iloc[mov_start_idx:mov_end_idx].copy()
    mov_result_chunks.append(mov_process_chunk(mov_chunk))

# Concatenate the result chunks into the final DataFrame
mov_result_df = pd.concat(mov_result_chunks)

  0%|          | 0/28 [00:00<?, ?it/s]/Users/meenakshigopalakrishnan/anaconda3/envs/characterPlaylistGenerator/lib/python3.12/site-packages/transformers/pipelines/text_classification.py:104: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(
  4%|▎         | 1/28 [40:25<18:11:31, 2425.60s/it]/Users/meenakshigopalakrishnan/anaconda3/envs/characterPlaylistGenerator/lib/python3.12/site-packages/transformers/pipelines/text_classification.py:104: UserWarning: `return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(
  7%|▋         | 2/28 [1:15:07<16:03:21, 2223.14s/it]/Users/meenakshigopalakrishnan/anaconda3/envs/characterPlaylistGenerator/lib/python3.12/site-packages/transformers/pipelines/text_classifica

In [13]:
mov_result_df.to_csv('movieEmotion.csv', index=False)

NameError: name 'mov_result_df' is not defined

In [14]:
mov_final_df = pd.read_csv('movieEmotion.csv')
song_final_df = pd.read_csv('songEmotion.csv')

mov_final_df.drop(columns=['Plot'], inplace=True)
song_final_df.drop(columns=['text'], inplace=True)

In [4]:
print(mov_final_df)
print(song_final_df)

       Release Year                                       Title  \
0              1951                             The 13th Letter   
1              1951  Abbott and Costello Meet the Invisible Man   
2              1951                             Ace in the Hole   
3              1951                    Across the Wide Missouri   
4              1951                Adventures of Captain Fabian   
...             ...                                         ...   
27865          2014                           The Water Diviner   
27866          2017                          Çalgı Çengi İkimiz   
27867          2017                                Olanlar Oldu   
27868          2017                            Non-Transferable   
27869          2017                          İstanbul Kırmızısı   

                      Director  \
0               Otto Preminger   
1               Charles Lamont   
2                 Billy Wilder   
3           William A. Wellman   
4             William Mar

In [15]:
mov_final_df.dropna(subset=['emotion_metrics'], inplace=True)
song_final_df.dropna(subset=['emotion_metrics'], inplace=True)

print(mov_final_df)
print(song_final_df)

       Release Year                                       Title  \
0              1951                             The 13th Letter   
1              1951  Abbott and Costello Meet the Invisible Man   
2              1951                             Ace in the Hole   
3              1951                    Across the Wide Missouri   
4              1951                Adventures of Captain Fabian   
...             ...                                         ...   
27865          2014                           The Water Diviner   
27866          2017                          Çalgı Çengi İkimiz   
27867          2017                                Olanlar Oldu   
27868          2017                            Non-Transferable   
27869          2017                          İstanbul Kırmızısı   

                      Director  \
0               Otto Preminger   
1               Charles Lamont   
2                 Billy Wilder   
3           William A. Wellman   
4             William Mar

In [16]:
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
from ast import literal_eval
import random
from scipy.sparse import csr_matrix


In [17]:
def convert_to_dict(emotion_str):
    return literal_eval(emotion_str)

# calculate emotion vector
def calculate_emotion_vector(emotion_dict):
    return np.array(list(emotion_dict.values()))

# calculate emotion vectors 
mov_final_df['Emotion Vector'] = mov_final_df['emotion_metrics'].apply(convert_to_dict).apply(calculate_emotion_vector)
song_final_df['Emotion Vector'] = song_final_df['emotion_metrics'].apply(convert_to_dict).apply(calculate_emotion_vector)


In [18]:
selected_movie = 'In the Mood for Love'
selected_movie_vector = mov_final_df.loc[mov_final_df['Title'] == selected_movie, 'Emotion Vector'].values[0]

# Convert the selected movie's emotion vector to a sparse matrix
selected_movie_vector_sparse = csr_matrix(selected_movie_vector)

# Convert emotion vectors of songs to a sparse matrix
songs_sparse_matrix = csr_matrix(song_final_df['Emotion Vector'].to_list())

# Calculate cosine similarity using sparse matrix operations
cosine_similarities = cosine_similarity(selected_movie_vector_sparse, songs_sparse_matrix)

# Extract top 200 similar songs
top_200_indices = np.argsort(cosine_similarities[0])[::-1][:200]
top_200_songs = song_final_df.iloc[top_200_indices]

# Randomly select 15 songs from the top 200
random.seed(42)  # for reproducibility, remove this line if you want different results each time
selected_songs = top_200_songs.sample(n=15)[['song', 'artist']]

print("Recommended Songs:")
for song, artist in selected_songs.values:
    print(f"{song} by {artist}")

Recommended Songs:
Rock Show by Lady Gaga
Ballad For A Friend by Bob Dylan
Give The Radio Back by Alice Cooper
Don't Leave Me by Green Day
The Fugitive by Iron Maiden
My Impression Now by Guided By Voices
Fear The Voices by Alice In Chains
Take Your Hand by Usher
Fallin' From The Sky by R. Kelly
Dangerous Times by Cher
Istanbul by Morrissey
World I Used To Know by Glen Campbell
Hurts Like Heaven by Coldplay
Somebody Might Wave Back by Waterboys
Scream Until You Like It by W.A.S.P.


In [99]:
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
from config import CLIENT_ID, CLIENT_SECRET
import requests

# Initialize Spotify client
client_credentials_manager = SpotifyClientCredentials(client_id=CLIENT_ID,client_secret=CLIENT_SECRET)
sp = spotipy.Spotify(client_credentials_manager=client_credentials_manager, requests_timeout=30000)

In [38]:
def get_genre(artist_name):
        # Search for the artist
    results = sp.search(q=f'artist:{artist_name}', type='artist', limit=1)
    
    # Check if any results were found
    if results['artists']['items']:
        artist_info = results['artists']['items'][0]
        if artist_info['genres']:
            return artist_info['genres'][0]  # Returning the first genre found
        else:
            return "Genre not available"
    else:
        return "Artist not found"

In [41]:
from tqdm import tqdm
import time

# Define rate limiting parameters
requests_per_minute_limit = 1000  # Adjust according to Spotify API rate limits
minute_window = 60  # seconds (1 minute)

# Track the time when the last request was made
last_request_time = None
requests_sent_this_minute = 0

# Dictionary to cache genre information for artists
genre_cache = {}

def add_genre_to_df(df):
    global last_request_time, requests_sent_this_minute

    genres = []
    for artist_name in tqdm(df['artist'], desc='Processing artists'):
        # Check if rate limit has been reached
        if requests_sent_this_minute >= requests_per_minute_limit:
            # Calculate the time to delay before making the next request
            time_since_last_request = time.time() - last_request_time
            time_to_wait = max(minute_window - time_since_last_request, 0)
            print(f"Rate limit reached. Waiting for {time_to_wait} seconds before making next request...")
            time.sleep(time_to_wait)
            requests_sent_this_minute = 0  # Reset requests count for the new minute

        # Check if genre information is cached
        if artist_name in genre_cache:
            genre = genre_cache[artist_name]
        else:
            # Make the request
            try:
                genre = get_genre(artist_name)
                genre_cache[artist_name] = genre  # Cache the genre information
            except Exception as e:
                print(f"Error fetching genre for {artist_name}: {e}")
                genre = None  # Set genre to None if retrieval fails

            # Update request tracking variables
            requests_sent_this_minute += 1
            last_request_time = time.time()

        genres.append(genre)

    df['Genre'] = genres

# Call the function with your DataFrame
add_genre_to_df(song_final_df)


Processing artists: 100%|██████████| 57650/57650 [01:31<00:00, 626.78it/s]  


In [42]:
print(song_final_df)

             artist                   song  \
0              ABBA  Ahe's My Kind Of Girl   
1              ABBA       Andante, Andante   
2              ABBA         As Good As New   
3              ABBA                   Bang   
4              ABBA       Bang-A-Boomerang   
...             ...                    ...   
57645  Ziggy Marley          Good Old Days   
57646  Ziggy Marley          Hand To Mouth   
57647          Zwan           Come With Me   
57648          Zwan                 Desire   
57649          Zwan              Heartsong   

                                         emotion_metrics  \
0      {'joy': 0.9988289208827446, 'anger': 0.0001545...   
1      {'joy': 0.6534017489030036, 'anger': 0.0038670...   
2      {'joy': 0.6008874079069335, 'anger': 0.0056411...   
3      {'joy': 0.008357059498882647, 'anger': 0.33226...   
4      {'joy': 0.01621546563623756, 'anger': 0.331428...   
...                                                  ...   
57645  {'joy': 0.9954145554

In [43]:
print(song_final_df['Genre'].unique())

['europop' 'eurodance' 'comic' 'british soul' 'album rock' 'soft rock'
 'opm' 'contemporary country' 'operatic pop' 'alternative metal'
 'bluegrass' 'new romantic' 'christian music' 'classical tenor'
 'adult standards' 'pop' 'classic opm' 'country rock' 'canadian pop'
 'boy band' 'Genre not available' 'baroque pop' 'british invasion'
 'britpop' 'movie tunes' 'disco' 'classic soul' 'alternative rock'
 'classic rock' 'reggae' 'glam metal' 'folk rock' 'dance pop'
 'heartland rock' 'classic oklahoma country' 'british folk' 'r&b' 'celtic'
 'blues' 'permanent wave' 'tin pan alley' 'arkansas country' 'neo mellow'
 'australian rock' 'jam band' 'country' 'art rock' 'big room' 'dance rock'
 'classic indonesian rock' 'desi hip hop' 'classic country pop'
 'classic praise' 'canadian hip hop' 'metal' 'rock-and-roll'
 'indietronica' 'glam rock' 'new wave' 'detroit hip hop' 'banda'
 'classic finnish rock' 'jazz blues' 'melodic drill' 'post-grunge' 'k-pop'
 'funk metal' 'gangster rap' 'punk' 'blues roc

In [46]:
edit_song_df = song_final_df[~song_final_df['Genre'].str.contains('metal', case='False')]

In [47]:
print(edit_song_df)

             artist                   song  \
0              ABBA  Ahe's My Kind Of Girl   
1              ABBA       Andante, Andante   
2              ABBA         As Good As New   
3              ABBA                   Bang   
4              ABBA       Bang-A-Boomerang   
...             ...                    ...   
57645  Ziggy Marley          Good Old Days   
57646  Ziggy Marley          Hand To Mouth   
57647          Zwan           Come With Me   
57648          Zwan                 Desire   
57649          Zwan              Heartsong   

                                         emotion_metrics  \
0      {'joy': 0.9988289208827446, 'anger': 0.0001545...   
1      {'joy': 0.6534017489030036, 'anger': 0.0038670...   
2      {'joy': 0.6008874079069335, 'anger': 0.0056411...   
3      {'joy': 0.008357059498882647, 'anger': 0.33226...   
4      {'joy': 0.01621546563623756, 'anger': 0.331428...   
...                                                  ...   
57645  {'joy': 0.9954145554

In [49]:
rows_to_delete = ['comic' 'opm' 'operatic pop' 'christian music' 'classical tenor' 'classic opm' 'movie tunes' 'glam metal' 'celtic' 'arkansas country'
 'classic indonesian rock' 'desi hip hop' 'banda' 'british comedy' 'flamenco'
 'glee club' 'cosmic american' 'canadian celtic' 'halloween' 'calypso'
 'german metal' 'ccm' 'Artist not found' 'apostolic worship' 'hawaiian' 'gospel' 'nu metal' 'danish metal' 'classic bollywood' 'comic metal' 'horror punk' 'fantasy metal' 'classic israeli pop'  'mahraganat' 'christian power metal' 'broadway'
 'death metal'  'celtic punk' 'celtic rock' 'medieval folk' "canadian children's music" 'worship' 'christian metal' 'boston metal' 'anime' 'black metal' 'classic texas country' 'comedy rock'  'dutch metal' 'old school thrash' 'banjo' 'nasheed' 'groove metal'
 'christian hardcore' 'industrial metal' 
 'christian alternative rock']

filtered_df = edit_song_df[~edit_song_df['Genre'].isin(rows_to_delete)]


In [51]:
filtered_df.to_csv('newSongEdited.csv', index=False)

In [84]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

In [91]:
from selenium import webdriver
import time

# Initialize Safari webdriver
driver = webdriver.Safari()

driver.get('https://chartmasters.org/most-streamed-artists-ever-on-spotify/')

time.sleep(5)

# Execute JavaScript to set the value of the dropdown menu to "United States"
driver.execute_script('''
    var dropdown = document.querySelector('select.wdt-multiselect-filter');
    dropdown.value = 'United States';
    dropdown.dispatchEvent(new Event('change', { bubbles: true }));
''')

time.sleep(5)

# Extract artist names
artist_names = driver.execute_script('''
    var names = [];
    document.querySelectorAll("table.dataTable tbody tr").forEach(function(row) {
        var name = row.querySelector("td:nth-child(3)").innerText;
        names.push(name.trim());
    });
    return names;
''')

for artist in artist_names:
    print(artist)

driver.quit()


Taylor Swift  
Up to date data
Drake  
Up to date data
Bad Bunny  
Up to date data
The Weeknd  
Up to date data
Ed Sheeran  
Up to date data
Ariana Grande  
Up to date data
Justin Bieber  
Up to date data
Eminem  
Up to date data
Post Malone  
Up to date data
BTS  
Up to date data
Kanye West  
Up to date data
J Balvin  
Up to date data
Billie Eilish  
Up to date data
Coldplay  
Up to date data
Travis Scott  
Up to date data
Dua Lipa  
Up to date data
Juice WRLD  
Up to date data
Rihanna  
Up to date data
Imagine Dragons  
Up to date data
XXXTENTACION  
Up to date data
Ozuna  
Up to date data
David Guetta  
Up to date data
Maroon 5  
Up to date data
Bruno Mars  
Up to date data
Khalid  
Up to date data


In [79]:
artists_to_add = [
    "Taylor Swift", "Ariana Grande", "Eminem", "Post Malone", "Kanye West", "Billie Eilish", "Travis Scott", 
    "Juice WRLD", "Imagine Dragons", "XXXTENTACION", "Maroon 5", "Bruno Mars", "Khalid", "Kendrick Lamar", 
    "Lana Del Rey", "Beyoncé", "Future", "Lady Gaga", "J. Cole", "Chris Brown", "The Chainsmokers", "Selena Gomez", 
    "Linkin Park", "Doja Cat", "Lil Uzi Vert", "SZA", "Marshmello", "Katy Perry", "Halsey", "Metro Boomin", 
    "21 Savage", "Milev Cyrus", "Olivia Rodrigo", "Twenty One Pilots", "Red Hot Chili Peppers", "Lil Baby", 
    "OneRepublic", "Camila Cabello", "Morgan Wallen", "Michael Jackson", "Jason Derulo", "Suicideboy$", 
    "Tyler, The Creator", "Pitbull", "Mac Miller", "Demi Lovato", "Metallica", "Pop Smoke", "Frank Ocean", 
    "The Neighbourhood", "Lil Wayne", "DaBaby", "YoungBoy Never Broke Again", "Charlie Puth", "Lil Nas X", 
    "PInk", "Young Thug", "Cardi B", "Romeo Santos", "Panic! At The Disco", "Fall Out Boy", "Wiz Khalifa", 
    "Nicky Jam", "NF", "Nirvana", "Luke Combs", "A Boogie Wit da Hoodie", "A$AP Rocky", "G-Eazy", "Major Lazer", 
    "Green Day", "Trippie Redd", "Bebe Rexha", "Tyga", "John Mayer", "Gunna", "Black Eyed Peas", "Fleetwood Mac", 
    "JAY-Z", "Lauv", "Justin Timberlake", "Britney Spears", "Logic", "50 Cent", "Kodak Black", "Playboi Carti", 
    "Guns N' Roses", "Migos", "Polo G", "DJ Khaled", "2Pac", "Machine Gun Kelly", "Ava Max", "Lil Peep", 
    "Kid Cudi", "Macklemore", "Becky G", "Diplo", "Mariah Carey", "Childish Gambino", "Flo Rida", "Usher", 
    "Fuerza Regida", "Melanie Martinez", "Russ", "Elvis Presley", "Foo Fighters", "System Of A Down", 
    "Frank Sinatra", "Meghan Trainor", "blink-182", "The Killers", "Snoop Dogg", "Arcangel", "Paramore", 
    "Madonna", "Slipknot", "blackbear", "Florida Georgia Line", "Creedence Clearwater Revival", 
    "The Notorious B.I.G.", "Bon Jovi", "Ty Dolla Sign", "Kali Uchis", "Bryson Tiller", "Luke Bryan", 
    "Whitney Houston", "Alicia Keys", "Ne-Yo", "Aventura", "Miguel", "Bruce Springsteen", "Kings of Leon", 
    "Bazzi", "Mitski", "Dr. Dre", "Sabrina Carpenter", "Five Finger Death Punch", "Kelly Clarkson", 
    "Aerosmith", "Cigarettes After Sex", "6ix9ine", "Kane Brown", "Brent Faiyaz", "Billy Joel", "Stevie Wonder", "Christina Aguilera", "Roddy Ricch", "The Strokes", 
    "Backstreet Boys", "Johnny Cash", "Disturbed", "6LACK", "Summer Walker", "Cheat Codes", 
    "Chris Stapleton", "Thomas Rhett", "Alec Benjamin", "Avenged Sevenfold", "Kesha", "Jason Aldean", 
    "Akon", "Fifth Harmony", "Prince Royce", "NLE Choppa", "Rod Wave", "Eslabon Armado", "Yeat", 
    "Marc Anthony", "Kehlani", "Steve Lacy", "Chance the Rapper", "Marvin Gaye", "H.E.R.", "Lil Yachty", 
    "Foster The People", "Pentatonix", "Pharrell Williams", "Offset", "Jhené Aiko", "Journey", 
    "Bob Dylan", "Zac Brown Band", "Anderson .Paak", "Jeremy Zucker", "The Doors", "Deftones", 
    "24kGoldn", "Bon Iver", "Sam Hunt", "Tim McGraw", "2 Chainz", "Quavo", "ScHoolboy Q", "Limp Bizkit", 
    "The Black Keys", "Trey Songz", "R.E.M.", "Papa Roach", "Giveon", "T.I.", "Why Don't We", 
    "Van Halen", "Madison Beer", "B.o.B", "TV Girl", "Evanescence", "Jimi Hendrix", "Rage Against The Machine", 
    "Oliver Tree", "Aminé", "The White Stripes", "A$AP Ferg", "Normani", "Shinedown", "KISS", "Chief Keef", 
    "Nas", "Dominic Fike", "Carrie Underwood", "All Time Low", "The Fray", "King Von", "Ella Fitzgerald", 
    "Sublime", "Alan Jackson"
]


In [98]:
import lyricsgenius
import pandas as pd

# Define your access token
token = ""

# Initialize Genius object with your access token
genius = lyricsgenius.Genius(token)


# Define a list of artists
artists = ["Taylor Swift", "Ariana Grande", "Eminem"]

# Define a function to fetch tracks and lyrics for an artist
def fetch_tracks_and_lyrics(artist_name, max_songs=50):
    # Search for songs by the artist, sorted by popularity
    artist = genius.search_artist(artist_name, max_songs=max_songs, sort="popularity")
    if artist:
        # Create a list to store the data
        data = []

        # Iterate over the songs by the artist
        for song in artist.songs:
            # Append the track details to the data list
            data.append({
                "Track": song.title,
                "Artist": artist_name,
                "Lyrics": song.lyrics
            })

        # Return the data list
        return data
    else:
        print(f"No songs found for {artist_name}")
        return []

# Define a function to fetch tracks and lyrics for multiple artists
def fetch_tracks_and_lyrics_for_artists(artist_list, max_songs_per_artist=50):
    # Create an empty list to store the data
    all_data = []

    # Iterate over the list of artists
    for artist_name in artist_list:
        print(f"Fetching songs for {artist_name}...")
        
        # Fetch tracks and lyrics for the current artist
        artist_data = fetch_tracks_and_lyrics(artist_name, max_songs=max_songs_per_artist)
        
        # Extend the list of all data with the data for the current artist
        all_data.extend(artist_data)

    # Create a DataFrame from the collected data
    df = pd.DataFrame(all_data)

    # Return the DataFrame
    return df

# Call the function to fetch tracks and lyrics for the list of artists
df_tracks_and_lyrics = fetch_tracks_and_lyrics_for_artists(artists)

# Display the DataFrame
print(df_tracks_and_lyrics)

Fetching songs for Taylor Swift...
Searching for songs by Taylor Swift...

Song 1: "All Too Well (10 Minute Version) (Taylor’s Version) [From The Vault]"
Song 2: "All Too Well (10 Minute Version) (Taylor’s Version) [Live Acoustic]"
Song 3: "​cardigan"
Song 4: "​exile"
Song 5: "Lover"
Song 6: "Is It Over Now? (Taylor’s Version) [From The Vault]"
Song 7: "​the 1"
Song 8: "​august"
Song 9: "Cruel Summer"
Song 10: "Look What You Made Me Do"
Song 11: "​tolerate it"
Song 12: "​champagne problems"
Song 13: "​betty"
Song 14: "Anti-Hero"
Song 15: "Blank Space"
Song 16: "Style"
Song 17: "You’re Losing Me (From The Vault)"
Song 18: "​my tears ricochet"
Song 19: "“Slut!” (Taylor’s Version) [From The Vault]"
Song 20: "End Game"
Song 21: "...Ready for It?"
Song 22: "You Need To Calm Down"
Song 23: "​willow"
Song 24: "ME!"
Song 25: "You’re On Your Own, Kid"
Song 26: "​invisible string"
Song 27: "Maroon"
Song 28: "We Are Never Ever Getting Back Together"
Song 29: "All Too Well"


Timeout: Request timed out:
HTTPSConnectionPool(host='genius.com', port=443): Read timed out. (read timeout=5)

In [39]:
df_tracks = pd.read_csv('topArtistsDF.csv')

In [40]:
df_tracks = df_tracks.drop_duplicates(subset=['Track', 'Artist'], keep='first')
version_keywords = ['live', 'acoustic', 'studio session', 'remix', 'demo', 'unplugged', 'the long pond studio sessions']

# Filter out rows containing version keywords in the 'Track' column
for keyword in version_keywords:
    df_tracks = df_tracks[~df_tracks['Track'].str.lower().str.contains(keyword.lower())]


In [9]:
import sys
sys.executable


'/Users/meenakshigopalakrishnan/anaconda3/envs/characterPlaylistGenerator/bin/python'

In [1]:
artists_to_add = [
    "Taylor Swift", "Ariana Grande", "Eminem", "Post Malone", "Kanye West", "Billie Eilish", "Travis Scott", 
    "Juice WRLD", "Imagine Dragons", "XXXTENTACION", "Maroon 5", "Bruno Mars", "Khalid", "Kendrick Lamar", 
    "Lana Del Rey", "Beyoncé", "Future", "Lady Gaga", "J. Cole", "Chris Brown", "The Chainsmokers", "Selena Gomez", 
    "Linkin Park", "Doja Cat", "Lil Uzi Vert", "SZA", "Marshmello", "Katy Perry", "Halsey", "Metro Boomin", 
    "21 Savage", "Miley Cyrus", "Olivia Rodrigo", "Twenty One Pilots", "Red Hot Chili Peppers", "Lil Baby", 
    "OneRepublic", "Camila Cabello", "Morgan Wallen", "Michael Jackson", "Jason Derulo", "Suicideboy$", 
    "Tyler, The Creator", "Pitbull", "Mac Miller", "Demi Lovato", "Metallica", "Pop Smoke", "Frank Ocean", 
    "The Neighbourhood", "Lil Wayne", "DaBaby", "YoungBoy Never Broke Again", "Charlie Puth", "Lil Nas X", 
    "PInk", "Young Thug", "Cardi B", "Romeo Santos", "Panic! At The Disco", "Fall Out Boy", "Wiz Khalifa", 
    "Nicky Jam", "NF", "Nirvana", "Luke Combs", "A Boogie Wit da Hoodie", "A$AP Rocky", "G-Eazy", "Major Lazer", 
    "Green Day", "Trippie Redd", "Bebe Rexha", "Tyga", "John Mayer", "Gunna", "Black Eyed Peas", "Fleetwood Mac", 
    "JAY-Z", "Lauv", "Justin Timberlake", "Britney Spears", "Logic", "50 Cent", "Kodak Black", "Playboi Carti", 
    "Guns N' Roses", "Migos", "Polo G", "DJ Khaled", "2Pac", "Machine Gun Kelly", "Ava Max", "Lil Peep", 
    "Kid Cudi", "Macklemore", "Becky G", "Diplo", "Mariah Carey", "Childish Gambino", "Flo Rida", "Usher", 
    "Fuerza Regida", "Melanie Martinez", "Russ", "Elvis Presley", "Foo Fighters", "System Of A Down", 
    "Frank Sinatra", "Meghan Trainor", "blink-182", "The Killers", "Snoop Dogg", "Arcangel", "Paramore", 
    "Madonna", "Slipknot", "blackbear", "Florida Georgia Line", "Creedence Clearwater Revival", 
    "The Notorious B.I.G.", "Bon Jovi", "Ty Dolla Sign", "Kali Uchis", "Bryson Tiller", "Luke Bryan", 
    "Whitney Houston", "Alicia Keys", "Ne-Yo", "Aventura", "Miguel", "Bruce Springsteen", "Kings of Leon", 
    "Bazzi", "Mitski", "Dr. Dre", "Sabrina Carpenter", "Five Finger Death Punch", "Kelly Clarkson", 
    "Aerosmith", "Cigarettes After Sex", "6ix9ine", "Kane Brown", "Brent Faiyaz", "Billy Joel", "Stevie Wonder", 
    "Christina Aguilera", "Roddy Ricch", "The Strokes", "Backstreet Boys", "Johnny Cash", "Disturbed", "6LACK", 
    "Summer Walker", "Cheat Codes", "Chris Stapleton", "Thomas Rhett", "Alec Benjamin", "Avenged Sevenfold", 
    "Kesha", "Jason Aldean", "Akon", "Fifth Harmony", "Prince Royce", "NLE Choppa", "Rod Wave", "Eslabon Armado", 
    "Yeat", "Marc Anthony", "Kehlani", "Steve Lacy", "Chance the Rapper", "Marvin Gaye", "H.E.R.", "Lil Yachty", 
    "Foster The People", "Pentatonix", "Pharrell Williams", "Offset", "Jhené Aiko", "Journey", "Bob Dylan", 
    "Zac Brown Band", "Anderson .Paak", "Jeremy Zucker", "The Doors", "Deftones", "24kGoldn", "Bon Iver", 
    "Sam Hunt", "Tim McGraw", "2 Chainz", "Quavo", "ScHoolboy Q", "Limp Bizkit", "The Black Keys", "Trey Songz", 
    "R.E.M.", "Papa Roach", "Giveon", "T.I.", "Why Don't We", "Van Halen", "Madison Beer", "B.o.B", "TV Girl", 
    "Evanescence", "Jimi Hendrix", "Rage Against The Machine", "Oliver Tree", "Aminé", "The White Stripes", 
    "A$AP Ferg", "Normani", "Shinedown", "KISS", "Chief Keef", "Nas", "Dominic Fike", "Carrie Underwood", 
    "All Time Low", "The Fray", "King Von", "Ella Fitzgerald", "Sublime", "Alan Jackson"
]

In [28]:
import os

GENIUS_API_KEY = os.environ.get('GENIUS_API_KEY')

In [7]:
import requests
from requests.exceptions import Timeout
import pandas as pd
from bs4 import BeautifulSoup
from tqdm import tqdm
import time

def extract_lyrics_from_html(lyrics_html):
    soup = BeautifulSoup(lyrics_html, 'html.parser')
    return soup.get_text(strip=True, separator='\n')

def get_lyrics(track_id, timeout=10, retries=3):
    url = "https://genius-song-lyrics1.p.rapidapi.com/song/lyrics/"
    querystring = {"id": track_id}
    headers = {
        "X-RapidAPI-Key": "8a9689b1eamshdd4a22bf92a824ap1fc9c8jsn30056e3b6560",
        "X-RapidAPI-Host": "genius-song-lyrics1.p.rapidapi.com"
    }
    for _ in range(retries):
        try:
            response = requests.get(url, headers=headers, params=querystring, timeout=timeout)
            if response.status_code == 200:
                response_data = response.json()
                if 'lyrics' in response_data and 'body' in response_data['lyrics']['lyrics']:
                    lyrics_html = response_data['lyrics']['lyrics']['body']['html']
                    return extract_lyrics_from_html(lyrics_html)
            else:
                print(f"Failed to fetch lyrics for track {track_id}. Status code: {response.status_code}")
        except (requests.RequestException, Timeout) as e:
            print(f"Request timed out for track {track_id}. Retrying...")
            continue
    return None

def fetch_lyrics(track_ids, timeout=10, retries=3):
    lyrics = []
    for track_id in tqdm(track_ids, desc="Fetching Lyrics"):
        print(f"Fetching lyrics for track {track_id}")
        lyrics.append(get_lyrics(track_id, timeout, retries))
    return lyrics

# Read your DataFrame or create it
df = pd.read_csv('GeniusDF4.csv')
track_ids = df["track_id"]

# Define chunk size
chunk_size = 100

# Fetch lyrics in chunks
for i in range(0, len(track_ids), chunk_size):
    chunk_track_ids = track_ids[i:i+chunk_size]
    chunk_lyrics = fetch_lyrics(chunk_track_ids)
    df.loc[i:i+len(chunk_lyrics)-1, "lyrics"] = chunk_lyrics
    
    # Save DataFrame after each chunk
    df.to_csv(f"GENIUSDF4_with_lyrics_chunk_{i//chunk_size}.csv", index=False)


Fetching Lyrics:   0%|          | 0/100 [00:00<?, ?it/s]

Fetching lyrics for track 7076626


Fetching Lyrics:   1%|          | 1/100 [00:00<01:17,  1.28it/s]

Fetching lyrics for track 7394358


Fetching Lyrics:   2%|▏         | 2/100 [00:01<01:03,  1.53it/s]

...

Fetching lyrics for track 201806


Fetching Lyrics:  99%|█████████▉| 99/100 [01:59<00:00,  1.01it/s]

Fetching lyrics for track 932074


Fetching Lyrics: 100%|██████████| 100/100 [02:00<00:00,  1.20s/it]


OSError: [Errno 28] No space left on device

In [3]:
df.to_csv('GeniusDF4.csv', index=False)

In [5]:
print(df)

                                              track_name  track_id  \
0      All Too Well (10 Minute Version) (Taylor’s Ver...   7076626   
1      All Too Well (10 Minute Version) (Taylor’s Ver...   7394358   
2                                               cardigan   5793984   
3                                                  exile   5793983   
4                                                  Lover   4508914   
...                                                  ...       ...   
17931                                           He Lives    427308   
17932                               I Still Like Bologna    427083   
17933                           We’re All God’s Children    786271   
17934                   (Who Says) You Can’t Have It All    426048   
17935                            Thank God for the Radio    426173   

        artist_name  artist_id  
0      Taylor Swift       1177  
1      Taylor Swift       1177  
2      Taylor Swift       1177  
3      Taylor Swift       1